In [5]:
import os
import h5py
import imageio
import numpy as np
import pandas as pd
import nibabel as nib
import seaborn as sns
from utils import metrics
from data import base_dataset

In [2]:
from utils import visualizer
import matplotlib.pylab as plt
from scipy.ndimage.measurements import center_of_mass

In [3]:
from matplotlib.backends.backend_agg import FigureCanvasAgg as FigureCanvas
from matplotlib.figure import Figure

In [10]:
Clinical_params = pd.DataFrame({'Group':[], 'SubjectID':[], 'rESS':[], 'cESS':[],
                                'RV_EDV_ml':[], 'RV_ESV_ml':[], 'RV_EF':[], 
                                'LV_EDV_ml':[], 'LV_ESV_ml':[], 'LV_EF':[], 'LV_mass_g':[], 'Frame':[]})


df = pd.read_csv('../private_data/MARTINOS.csv', index_col=0)

Err = []
Ecc = []
for subject_index in df.index: 
    group = df.iloc[subject_index].Group
    sid   = df.iloc[subject_index].SubjectID
    
    if group == 'DM':
        M_nifti = nib.load('../private_data_results/MARTINOS/MSTAT_DM_VOL%d_V1_segmentation.nii'%(sid))
        u_HF = h5py.File('../private_data_results/MARTINOS/MSTAT_DM_VOL%d_V1_motion.h5'%(sid), 'r')
    elif sid > 100:
        M_nifti = nib.load('../private_data_results/MARTINOS/MSTAT_%d_V2_segmentation.nii'%(sid))
        u_HF = h5py.File('../private_data_results/MARTINOS/MSTAT_%d_V2_motion.h5'%(sid), 'r')
    else:
        try:
            M_nifti = nib.load('../private_data_results/MARTINOS/MSTAT_VOL%d_V1_segmentation.nii'%(sid))
            u_HF = h5py.File('../private_data_results/MARTINOS/MSTAT_VOL%d_V1_motion.h5'%(sid), 'r')
        except:
            M_nifti = nib.load('../private_data_results/MARTINOS/MSTAT_VOL%d_V2_segmentation.nii'%(sid))
            u_HF = h5py.File('../private_data_results/MARTINOS/MSTAT_VOL%d_V2_motion.h5'%(sid), 'r')
    
    
    M_nifti = nifti_dataset.resample_nifti(M_nifti, in_plane_resolution_mm=1.25, number_of_slices=16)
    
    m  = M_nifti.get_fdata()
    u  = load_HF(u_HF)
    
    center = center_of_mass(m[:,:,:,0]==3)
    
    u=base_dataset._roll2center_crop(u,center)
    m=base_dataset._roll2center_crop(m,center)
    
    esid = (m[:,:,3:-3]==3).sum(axis=(0,1,2)).argmin()
    
    
    for t in [esid]:
        # CALCULATE PARAMS AT END-SYSTOLE ONLY
        
        E = strain.MyocardialStrain(m[:,:,:,0],u[:,:,:,:,t])
        E.calculate_strain()

        rESS = E.Err[E.mask_rot==2].mean()
        cESS = E.Ecc[E.mask_rot==2].mean()
        
        print(group, rESS, cESS)

        
    break

DM 0.27433953948483814 -0.17179240013074187


In [11]:
import numpy as np
from scipy.ndimage import rotate
from scipy.ndimage import gaussian_filter
from scipy.interpolate import interp1d, interp2d
from scipy.ndimage.measurements import center_of_mass

class MyocardialStrain():
    
    def __init__(self, mask, flow):
                
        self.mask  = mask
        self.flow  = flow
        
        assert len(mask.shape) == 3
        assert len(flow.shape) == 4
        assert mask.shape == flow.shape[:3]
        assert flow.shape[-1] == 3
        
    def calculate_strain(self, dx=1, dy=1, dz=1, lv_label=3):
        
        cx, cy, cz = center_of_mass(self.mask==lv_label)
        nx, ny, nz = self.mask.shape
        
        self.flow_rot = _roll_to_center(self.flow, cx, cy)
        self.mask_rot = _roll_to_center(self.mask, cx, cy)

        ux, uy, uz  = np.array_split(self.flow_rot, 3, -1)
        Uxx,Uxy,Uxz = np.gradient(np.squeeze(ux),dx,dy,dz)
        Uyx,Uyy,Uyz = np.gradient(np.squeeze(uy),dx,dy,dz)
        Uzx,Uzy,Uzz = np.gradient(np.squeeze(uz),dx,dy,dz)

        self.E_cart = np.zeros((nx,ny,nz,3,3))
        for i in range(nx):
            for j in range(ny):
                for k in range(nz):
                    Ugrad = [[Uxx[i,j,k], Uxy[i,j,k], Uxz[i,j,k]], 
                             [Uyx[i,j,k], Uyy[i,j,k], Uyz[i,j,k]],
                             [Uzx[i,j,k], Uzy[i,j,k], Uzz[i,j,k]]]
                    F = np.array(Ugrad) + np.identity(3)
                    e = 0.5*(np.matmul(F.T, F) - np.identity(3))
                    self.E_cart[i,j,k] += e

        self.Ezz = self.E_cart[:,:,:,2,2]
        self.Err, self.Ecc = self._convert_to_polar(self.E_cart[:,:,:,:2,:2])

        
        
        
    def _convert_to_polar(self, E):

        phi = _polar_grid(*E.shape[:2])[0]
        Err = np.zeros(self.mask.shape)
        Ecc = np.zeros(self.mask.shape)
        for k in range(self.mask.shape[-1]):
            cos = np.cos(np.deg2rad(phi))
            sin = np.sin(np.deg2rad(phi))
        
            Exx, Exy, Eyx, Eyy = E[:,:,k,0,0],E[:,:,k,0,1],E[:,:,k,1,0],E[:,:,k,1,1]
            Err[:,:,k] +=  cos*( cos*Exx+sin*Exy) +sin*( cos*Eyx+sin*Eyy)
            Ecc[:,:,k] += -sin*(-sin*Exx+cos*Exy) +cos*(-sin*Eyx+cos*Eyy)

        return Err, Ecc
    
   

def _roll(x, rx, ry):
    x = np.roll(x, rx, axis=0)
    return np.roll(x, ry, axis=1)

def _roll_to_center(x, cx, cy):
    nx, ny = x.shape[:2]
    return _roll(x,  int(nx//2-cx), int(ny//2-cy))

def _polar_grid(nx=128, ny=128):
    x, y = np.meshgrid(np.linspace(-nx//2, nx//2, nx), np.linspace(-ny//2, ny//2, ny))
    phi  = (np.rad2deg(np.arctan2(y, x)) + 180).T
    r    = np.sqrt(x**2+y**2+1e-8)
    return phi, r

In [12]:
E = MyocardialStrain(m[:,:,:,0],u[:,:,:,:,t])
E.calculate_strain()

rESS = E.Err[E.mask_rot==2].mean()
cESS = E.Ecc[E.mask_rot==2].mean()

print(group, rESS, cESS)

DM 0.27433953948483814 -0.17179240013074187


In [13]:
mask = m[:,:,:,0]
flow = u[:,:,:,:,t]

In [19]:
lv_label = 3

cx, cy, cz = center_of_mass(mask==lv_label)
nx, ny, nz = mask.shape

cx, cy, cz

flow_rot = _roll_to_center(flow, cx, cy)
mask_rot = _roll_to_center(mask, cx, cy)

dx=1; dy=1; dz=1

ux, uy, uz  = np.array_split(flow_rot, 3, -1)
Uxx,Uxy,Uxz = np.gradient(np.squeeze(ux),dx,dy,dz)
Uyx,Uyy,Uyz = np.gradient(np.squeeze(uy),dx,dy,dz)
Uzx,Uzy,Uzz = np.gradient(np.squeeze(uz),dx,dy,dz)

In [53]:
def_grad = np.array([[Uxx,Uxy,Uxz],
                     [Uyx,Uyy,Uyz],
                     [Uzx,Uzy,Uzz]])

In [54]:
I = np.identity(3)[:,:,None,None,None]
I = np.repeat(I,repeats=128, axis=2)
I = np.repeat(I,repeats=128, axis=3)
I = np.repeat(I,repeats=16, axis=4)

In [62]:
F = def_grad + I

In [64]:
for i in range(nx):
    for j in range(ny):
        for k in range(nz):
            
            Ugrad = [[Uxx[i,j,k], Uxy[i,j,k], Uxz[i,j,k]], 
                     [Uyx[i,j,k], Uyy[i,j,k], Uyz[i,j,k]],
                     [Uzx[i,j,k], Uzy[i,j,k], Uzz[i,j,k]]]
            
            Fijk = np.array(Ugrad) + np.identity(3)
            
            assert (Fijk == F[:,:,i,j,k]).all()

In [58]:
Fijk

array([[1., 0., 0.],
       [0., 1., 0.],
       [0., 0., 1.]])

In [59]:
F[:,:,i,j,k]

array([[0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.]])

In [ ]:
F = np.array(Ugrad) + np.identity(3)
            e = 0.5*(np.matmul(F.T, F) - np.identity(3))
            self.E_cart[i,j,k] += e


In [35]:
np.repeat?

In [7]:
# Manuel A. Morales (moralesq@mit.edu)
# Harvard-MIT Department of Health Sciences & Technology  
# Athinoula A. Martinos Center for Biomedical Imaging

import os
import h5py
import glob
import warnings
import numpy as np
import nibabel as nib

from dipy.align.reslice import reslice
from data.base_dataset import BaseDataset, Transforms
from data.image_folder import make_dataset


class H5PYDataset(BaseDataset):

    def __init__(self, opt):
        BaseDataset.__init__(self, opt)
        self.filenames = sorted(make_dataset(opt.dataroot, opt.max_dataset_size, 'H5PY'))
    
    def __len__(self):
        return len(self.filenames)
                
    def __getitem__(self, idx):      

        HF = h5py.File(self.filenames[idx], 'r')
        

In [8]:
import h5py
from utils import strain
from data import nifti_dataset

In [9]:
def load_HF(HF):
    output = []
    for frame_id in range(len(HF.keys())):
        key = 'frame_%d'%(frame_id)
        for subkey in HF[key].keys():
            output += [np.array(HF[key][subkey])]

    HF.close()
    return np.stack(output,-1)